In [ ]:
from google.colab import files
files.upload()


Saving a1.wav to a1.wav
Saving a2.wav to a2.wav


{'a1.wav': b'RIFF\xf6\'\x0c\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00\x80\xbb\x00\x00\x00w\x01\x00\x02\x00\x10\x00LIST\x1a\x00\x00\x00INFOISFT\x0e\x00\x00\x00Lavf60.16.100\x00data\xb0\'\x0c\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\xff\xff\xff\xff\x00\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x00\x00\x00\x00\xff\xff\x00\x00\x01\x00\x01\x00\x01\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x01\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\

In [ ]:
from google.colab import files
files.upload()

Saving a1.txt to a1.txt


{'a1.txt': b'this is the file i want to convert into short file'}

In [ ]:
from google.colab import files
files.upload()

Saving a2.txt to a2.txt


{'a2.txt': b'this is the science project'}

In [ ]:
!ls

a1.txt	a1.wav	a2.txt	a2.wav	sample_data


In [ ]:
!pip install -q openai-whisper vosk jiwer


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 803.2/803.2 kB 34.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 98.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 87.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 170.5/170.5 MB 5.8 MB/s eta 0:00:00


In [ ]:
!wget -q https://alphacephei.com/vosk/models/vosk-model-small-en-us-0.15.zip
!unzip -o vosk-model-small-en-us-0.15.zip


Archive:  vosk-model-small-en-us-0.15.zip
   creating: vosk-model-small-en-us-0.15/
   creating: vosk-model-small-en-us-0.15/am/
  inflating: vosk-model-small-en-us-0.15/am/final.mdl  
   creating: vosk-model-small-en-us-0.15/graph/
  inflating: vosk-model-small-en-us-0.15/graph/disambig_tid.int  
  inflating: vosk-model-small-en-us-0.15/graph/HCLr.fst  
  inflating: vosk-model-small-en-us-0.15/graph/Gr.fst  
   creating: vosk-model-small-en-us-0.15/graph/phones/
  inflating: vosk-model-small-en-us-0.15/graph/phones/word_boundary.int  
   creating: vosk-model-small-en-us-0.15/conf/
  inflating: vosk-model-small-en-us-0.15/conf/model.conf  
  inflating: vosk-model-small-en-us-0.15/conf/mfcc.conf  
   creating: vosk-model-small-en-us-0.15/ivector/
  inflating: vosk-model-small-en-us-0.15/ivector/splice.conf  
  inflating: vosk-model-small-en-us-0.15/ivector/final.dubm  
  inflating: vosk-model-small-en-us-0.15/ivector/global_cmvn.stats  
  inflating: vosk-model-small-en-us-0.15/ivector/f

In [ ]:
import whisper
from vosk import Model, KaldiRecognizer
from jiwer import wer
import wave
import json


In [ ]:
whisper_model = whisper.load_model("base")


100%|████████████████████████████████████████| 139M/139M [00:01<00:00, 105MiB/s]


In [ ]:
def whisper_transcribe(audio):
    result = whisper_model.transcribe(audio)
    return result["text"].lower()


In [ ]:
vosk_model = Model("vosk-model-small-en-us-0.15")


In [ ]:
def vosk_transcribe(audio):
    wf = wave.open(audio, "rb")
    rec = KaldiRecognizer(vosk_model, wf.getframerate())
    rec.SetWords(True)

    text = ""
    while True:
        data = wf.readframes(4000)
        if len(data) == 0:
            break
        if rec.AcceptWaveform(data):
            part = json.loads(rec.Result())
            text += part.get("text", "") + " "

    final = json.loads(rec.FinalResult())
    text += final.get("text", "")
    return text.lower()


In [ ]:
def load_reference(file):
    with open(file, "r") as f:
        return f.read().lower()


In [ ]:
pairs = [
    ("a1.wav", "a1.txt"),
    ("a2.wav", "a2.txt")
]

for audio, ref in pairs:
    ref_text = load_reference(ref)

    whisper_text = whisper_transcribe(audio)
    vosk_text = vosk_transcribe(audio)

    print(f"\nAudio: {audio}")
    print("Whisper WER:", wer(ref_text, whisper_text))
    print("Vosk WER:", wer(ref_text, vosk_text))


/usr/local/lib/python3.12/dist-packages/whisper/transcribe.py:132: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")



Audio: a1.wav
Whisper WER: 0.2727272727272727
Vosk WER: 0.5454545454545454


/usr/local/lib/python3.12/dist-packages/whisper/transcribe.py:132: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")



Audio: a2.wav
Whisper WER: 0.2
Vosk WER: 0.0


In [ ]:
# Store WER values manually from previous output
whisper_wers = [0.2727272727272727, 0.2]
vosk_wers = [0.5454545454545454, 0.0]

avg_whisper = sum(whisper_wers) / len(whisper_wers)
avg_vosk = sum(vosk_wers) / len(vosk_wers)

print("================ FINAL RESULT ================")
print("Average Whisper WER:", avg_whisper)
print("Average Vosk WER:", avg_vosk)

if avg_whisper < avg_vosk:
    print("✅ BEST MODEL: WHISPER (Lower WER)")
elif avg_vosk < avg_whisper:
    print("✅ BEST MODEL: VOSK (Lower WER)")
else:
    print("⚠️ BOTH MODELS PERFORM EQUALLY")


================ FINAL RESULT ================
Average Whisper WER: 0.23636363636363636
Average Vosk WER: 0.2727272727272727
✅ BEST MODEL: WHISPER (Lower WER)
